*** SPARK SQL ***

## The Data

![img](http://training.databricks.com/databricks_guide/USDA_logo.png)

The first of the two datasets that we will be working with is the **Farmers Markets Directory and Geographic Data**. This dataset contains information on the longitude and latitude, state, address, name, and zip code of farmers markets in the United States. The raw data is published by the Department of Agriculture. The version on the data that is found in Databricks (and is used in this tutorial) was updated by the Department of Agriculture on Dec 01, 2015.

![img](http://training.databricks.com/databricks_guide/irs-logo.jpg)

The second dataset we will be working with is the **SOI Tax Stats - Individual Income Tax Statistics - ZIP Code Data (SOI)**. This study provides detailed tabulations of individual income tax return data at the state and ZIP code level and is provided by the IRS. This repository only has a sample of the data: 2013 and includes "AGI". The ZIP Code data shows selected income and tax items classified by State, ZIP Code, and size of adjusted gross income. Data is based on individual income tax returns filed with the IRS and is available for Tax Years 1998, 2001, 2004 through 2013.


In [0]:
# Read The data
taxes2013 = (spark.read
  .option("header", "true")
  .csv("dbfs:/databricks-datasets/data.gov/irs_zip_code_data/data-001/2013_soi_zipcode_agi.csv"))

markets = (spark.read
  .option("header", "true")
  .csv("dbfs:/databricks-datasets/data.gov/farmers_markets_geographic_data/data-001/market_data.csv"))

In [0]:
import math
def haversine(lat1, lon1, lat2, lon2):
    # convert decimal degrees to radians
    lat1, lon1, lat2, lon2 = map(math.radians, [lat1, lon1, lat2, lon2])
    # haversine formula
    dlat = lat2 - lat1 
    dlon = lon2 - lon1 
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2
    c = 2 * math.asin(math.sqrt(a))
    r = 3956  # Radius of earth in miles. Use 6371 for kilometers.
    return c * r

from pyspark.sql.functions import udf, col
from pyspark.sql.types import DoubleType

# Set your target wealthy zip code's latitude and longitude
target_lat = 40.7128    # example latitude
target_lon = -74.0060   # example longitude

from pyspark.sql.functions import col, udf
from pyspark.sql.types import DoubleType

# Define a function for Euclidean distance calculation
def euclidean_distance(lat1, lon1, lat2, lon2):
    return ((lat1 - lat2)**2 + (lon1 - lon2)**2)**0.5

# Register the function as a UDF
distance_udf = udf(euclidean_distance, DoubleType())

# Add the new column using the UDF
markets = markets.withColumn("distance_to_wealthy", distance_udf(
    col("Market_Lat"), col("Market_Long"), col("Rich_ZIP_Lat"), col("Rich_ZIP_Long")
))




In [0]:
# Register spark SQL tables

taxes2013.createOrReplaceTempView("taxes2013")
markets.createOrReplaceTempView("markets")

In [0]:
%sql
DROP TABLE IF EXISTS cleaned_taxes;

CREATE OR REPLACE TABLE cleaned_taxes AS
SELECT state, int(zipcode / 10) as zipcode, 
  int(mars1) as single_returns, 
  int(mars2) as joint_returns, 
  int(numdep) as numdep, 
  double(A02650) as total_income_amount,
  double(A00300) as taxable_interest_amount,
  double(a01000) as net_capital_gains,
  double(a00900) as biz_net_income
FROM taxes2013;


num_affected_rows num_inserted_rows

In [0]:
sqlContext.cacheTable("cleaned_taxes")

# Convert back to a dataset from a table
cleanedTaxes = spark.sql("SELECT * FROM cleaned_taxes")

summedTaxes = cleanedTaxes.groupBy("zipcode").sum() # because of AGI, where groups income groups are broken out 

cleanedMarkets = (markets
  .selectExpr("*", "int(zip / 10) as zipcode")
  .groupBy("zipcode")
  .count()
  .selectExpr("double(count) as count", "zipcode as zip"))
#  selectExpr is short for Select Expression - equivalent to what we
#  might be doing in SQL SELECT expression

joined = (cleanedMarkets.join(summedTaxes, cleanedMarkets.zip == summedTaxes.zipcode, "outer"))

In [0]:
display(cleanedMarkets)

count zip 5.0 4900 2.0 7240 8.0 4818 1.0 9852 2.0 5300 5.0 2122 2.0 9900 1.0 8592 1.0 1580 1.0 3175 1.0 7754 2.0 6336 1.0 7833 1.0 7340 1.0 6466 4.0 6620 1.0 1342 2.0 496 1.0 5156 1.0 4101 1.0 3918 2.0 8086 8.0 1460 2.0 9564 1.0 3226 7.0 1522 7.0 540 1.0 1483 2.0 623 5.0 3179 1.0 6773 1.0 1896 1.0 5614 4.0 2811 1.0 1990 1.0 8105 2.0 2387 3.0 3761 1.0 8407 3.0 9454 4.0 1303 2.0 2821 2.0 7850 2.0 1650 1.0 3213 1.0 1903 2.0 5984 3.0 1143 1.0 8222 2.0 3704 1.0 2393 2.0 2721 2.0 2525 2.0 4042 4.0 2231 1.0 5482 3.0 3220 1.0 7910 2.0 5223 1.0 9071 2.0 5155 1.0 7120 1.0 5308 2.0 137 1.0 7066 1.0 2025 1.0 5740 2.0 5217 3.0 6301 1.0 4000 3.0 6934 3.0 2833 1.0 2392 2.0 6154 2.0 9597 1.0 3566 2.0 7576 1.0 65 1.0 2655 1.0 9403 2.0 9775 2.0 9206 1.0 5157 1.0 4307 1.0 3377 1.0 8501 7.0 9675 5.0 2802 14.0 9344 2.0 3028 1.0 7810 3.0 3631 1.0 8701 1.0 9575 2.0 6890 1.0 2247 2.0 804 2.0 255 2.0 6864 2.0 7404 2.0 6176 2.0 1157 1.0 5110 1.0 6866 1.0 4357 3.0 6010 7.0 9721 4.0 133 2.0 6376 2.0 853 1.0 5140 3.0 5061 1.0 3242 1.0 4612 4.0 8950 1.0 8450 1.0 4838 1.0 8534 2.0 3306 1.0 8409 1.0 2542 1.0 5670 2.0 8051 6.0 322 4.0 3703 2.0 4531 3.0 9258 1.0 6142 1.0 7283 3.0 9470 1.0 5030 1.0 78 1.0 4697 1.0 1808 1.0 9867 1.0 5920 1.0 2848 2.0 9324 3.0 5543 1.0 633 3.0 4512 3.0 5222 1.0 2625 1.0 1533 2.0 2971 1.0 6145 1.0 4725 4.0 6108 1.0 3601 1.0 4401 1.0 4923 2.0 1212 3.0 6913 1.0 2513 2.0 2835 3.0 9006 1.0 375 1.0 4713 4.0 9968 1.0 8350 1.0 4762 5.0 9730 1.0 5235 1.0 6157 1.0 1700 1.0 1331 1.0 7865 3.0 8003 1.0 683 2.0 5771 1.0 6754 3.0 108 1.0 8755 2.0 744 3.0 2606 2.0 2200 2.0 1344 4.0 211 3.0 530 3.0 193 1.0 4517 9.0 4321 3.0 7103 1.0 1404 2.0 642 1.0 6124 1.0 1537 3.0 6204 1.0 4132 3.0 6005 1.0 796 1.0 8354 1.0 9209 1.0 4263 1.0 3235 2.0 1500 3.0 4865 3.0 126 2.0 6933 2.0 101 1.0 7602 1.0 2261 3.0 6056 1.0 9957 2.0 2771 2.0 2003 2.0 772 1.0 1378 3.0 2907 1.0 8536 1.0 5597 1.0 6741 13.0 3313 1.0 2662 1.0 830 1.0 6460 1.0 5452 1.0 3611 3.0 5490 2.0 8243 1.0 8325 3.0 3026 2.0 5447 2.0 385 2.0 2212 2.0 7550 1.0 874 1.0 4637 2.0 3008 1.0 8001 1.0 8412 4.0 1201 4.0 1441 1.0 9781 2.0 7800 1.0 210 2.0 2180 4.0 6095 3.0 183 1.0 3445 1.0 1175 3.0 3234 1.0 1426 4.0 9207 1.0 7460 1.0 2313 1.0 7522 2.0 9714 1.0 1031 1.0 3685 1.0 3650 3.0 4424 2.0 8090 3.0 2018 2.0 2842 1.0 9081 2.0 1051 1.0 1621 1.0 7501 3.0 8500 1.0 8123 2.0 1510 4.0 8410 2.0 7306 1.0 4230 1.0 1243 1.0 497 1.0 3885 1.0 7147 4.0 2962 5.0 4107 3.0 8132 2.0 5845 2.0 1156 2.0 3706 2.0 2945 1.0 1752 1.0 5884 2.0 784 1.0 406 1.0 9113 1.0 787 1.0 1030 2.0 1489 1.0 5880 2.0 4843 3.0 2752 2.0 3626 2.0 3296 3.0 2240 2.0 5854 1.0 1708 2.0 1307 1.0 4925 1.0 1276 1.0 7838 1.0 9366 1.0 6288 1.0 2015 2.0 9029 3.0 9538 1.0 1480 2.0 9700 7.0 2871 2.0 3595 1.0 2526 1.0 6863 1.0 3013 1.0 8130 2.0 76 2.0 9551 2.0 4695 1.0 6705 1.0 3264 2.0 3346 2.0 3359 3.0 5040 4.0 5505 1.0 4700 2.0 2758 2.0 688 1.0 1871 2.0 6936 1.0 8411 3.0 3811 4.0 3211 2.0 6473 1.0 4758 1.0 3411 1.0 1634 2.0 6011 1.0 8980 2.0 2754 3.0 9935 2.0 2650 1.0 5066 1.0 2857 1.0 2610 2.0 9890 3.0 626 2.0 5396 1.0 5993 2.0 2750 1.0 6040 3.0 4408 1.0 2331 4.0 8053 1.0 7192 1.0 4830 1.0 51333 2.0 384 3.0 1294 3.0 5647 2.0 4876 1.0 9027 1.0 5258 1.0 7895 1.0 5160 1.0 9615 1.0 5024 1.0 4866 6.0 4538 2.0 6831 2.0 7290 9.0 2322 3.0 1350 5.0 3370 2.0 5214 1.0 5764 1.0 192 2.0 271 2.0 9842 1.0 5606 1.0 3183 1.0 743 1.0 1135 3.0 9547 1.0 8312 1.0 3010 2.0 4036 3.0 253 2.0 2727 1.0 2076 3.0 1280 2.0 9286 1.0 1210 3.0 2809 1.0 9205 1.0 8290 2.0 2804 1.0 5480 5.0 5448 1.0 7516 6.0 9840 3.0 460 2.0 3512 5.0 1056 2.0 2323 1.0 3456 6.0 6110 1.0 5080 1.0 7239 1.0 1890 2.0 8022 2.0 8260 5.0 236 4.0 5401 3.0 6030 2.0 2062 2.0 103 3.0 9254 6.0 9712 1.0 7311 1.0 329 1.0 4104 2.0 2629 1.0 2497 1.0 8115 1.0 2496 3.0 4874 1.0 4523 2.0 7940 3.0 1260 3.0 6810 2.0 3741 2.0 9601 1.0 6201 3.0 9966 11.0 1046 1.0 2409 3.0 3054 1.0 5322 1.0 7005 1.0 7786 1.0 4305 2.0 9824 1.0 6267 1.0 2723 1.0 8570 1.0 9103 1.0 3207 13.0 2920 2.0 5003 2.0 2090 3.0 9741 4.0 2701 3.0 5465 1.0 2684 2

In [0]:
display(joined)

count zip zipcode sum(zipcode) sum(single_returns) sum(joint_returns) sum(numdep) sum(total_income_amount) sum(taxable_interest_amount) sum(net_capital_gains) sum(biz_net_income) 1009.0 null null null null null null null null null null 1.0 0 0 0 66430180 52885400 96500590 9.274122025E9 8.271064E7 3.99567789E8 3.10024683E8 1.0 3 null null null null null null null null null 4.0 60 null null null null null null null null null 1.0 61 null null null null null null null null null 2.0 62 null null null null null null null null null 1.0 63 null null null null null null null null null 1.0 65 null null null null null null null null null 4.0 66 null null null null null null null null null 4.0 67 null null null null null null null null null 4.0 68 null null null null null null null null null 2.0 70 null null null null null null null null null 1.0 71 null null null null null null null null null 2.0 72 null null null null null null null null null 2.0 73 null null null null null null null null null 3.0 75 null null null null null null null null null 2.0 76 null null null null null null null null null 1.0 77 null null null null null null null null null 1.0 78 null null null null null null null null null 1.0 79 null null null null null null null null null 1.0 90 null null null null null null null null null 1.0 91 null null null null null null null null null 1.0 96 null null null null null null null null null 5.0 100 100 3000 14570 11140 14180 1897431.0 15257.0 62938.0 82567.0 2.0 101 101 2424 6710 4100 7320 584312.0 2868.0 8553.0 12935.0 3.0 102 102 3060 17720 12600 15840 1932081.0 12643.0 33077.0 63570.0 2.0 103 103 5562 9000 7870 9020 1175081.0 7565.0 24622.0 42659.0 3.0 104 104 624 8370 3820 10160 658257.0 3655.0 8273.0 20792.0 2.0 105 105 3150 8590 7130 8470 1042641.0 7468.0 17518.0 31384.0 3.0 106 106 2544 10140 6000 7330 1164956.0 10636.0 45366.0 67045.0 1.0 107 107 3852 9040 7620 8620 1230785.0 10053.0 23110.0 43253.0 3.0 108 108 3888 20220 14780 21130 2263206.0 15173.0 35177.0 65399.0 1.0 109 109 1962 4160 4240 5090 782631.0 6835.0 29191.0 32579.0 3.0 110 110 4620 23270 10930 38260 2410836.0 21921.0 111191.0 87619.0 null null 111 1332 6440 3810 7490 596115.0 2824.0 3245.0 11472.0 null null 112 1344 2490 1790 2460 250951.0 989.0 831.0 5816.0 null null 115 690 1880 750 2900 120178.0 420.0 299.0 2329.0 2.0 120 120 720 11730 6990 10650 1104177.0 8164.0 19952.0 29908.0 1.0 122 122 4392 5570 4130 5090 566792.0 3902.0 7579.0 14745.0 8.0 123 123 3690 5520 4040 4410 640316.0 6422.0 42429.0 36455.0 1.0 124 124 2232 5090 3440 4290 511879.0 5434.0 18268.0 21050.0 1.0 125 125 5250 1720 1460 1390 278982.0 2462.0 16027.0 16113.0 3.0 126 126 1512 1700 1600 1600 321658.0 4552.0 25628.0 19457.0 null null 127 762 150 210 160 24818.0 94.0 190.0 812.0 1.0 130 130 780 4640 2680 3610 398144.0 3220.0 7027.0 15878.0 4.0 133 133 3990 4360 3470 4470 439144.0 2178.0 9489.0 15133.0 1.0 134 134 4824 1790 1640 1810 227607.0 1241.0 7598.0 8975.0 null null 135 2430 1240 1050 1030 143066.0 773.0 4206.0 6599.0 3.0 136 136 4080 2840 2550 3170 310602.0 1358.0 4420.0 12136.0 2.0 137 137 4932 5140 3280 3770 496813.0 4074.0 14707.0 23776.0 3.0 142 142 852 8680 5140 10680 750077.0 3215.0 6657.0 19766.0 3.0 143 143 4290 4960 4090 5540 612770.0 2835.0 5935.0 17180.0 null null 144 864 4650 3090 4710 421055.0 2119.0 3419.0 12072.0 4.0 145 145 3480 14520 12000 18150 2340633.0 15976.0 94626.0 84718.0 2.0 146 146 5256 11110 10920 14040 1810611.0 8907.0 43209.0 63177.0 1.0 147 147 2646 4330 3980 5410 582230.0 2716.0 8801.0 18869.0 4.0 150 150 5400 11740 10440 13400 1730649.0 8516.0 30780.0 57549.0 2.0 151 151 4530 8480 7070 10200 1240121.0 4793.0 18573.0 34434.0 2.0 152 152 6384 11680 10900 14160 1804149.0 9270.0 30818.0 56775.0 3.0 153 153 5508 8400 8050 10730 1547512.0 8065.0 36668.0 56348.0 2.0 154 154 4620 13450 13840 19230 2710097.0 15183.0 63762.0 92712.0 null null 155 930 3970 2180 4880 327997.0 1567.0 1856.0 8399.0 3.0 156 156 5616 11460 11260 14750 1911354.0 9032.0 36270.0 6

deal with na values

In [0]:
prepped = joined.na.fill(0)
display(prepped)

count zip zipcode sum(zipcode) sum(single_returns) sum(joint_returns) sum(numdep) sum(total_income_amount) sum(taxable_interest_amount) sum(net_capital_gains) sum(biz_net_income) 1009.0 0 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 0 0 0 66430180 52885400 96500590 9.274122025E9 8.271064E7 3.99567789E8 3.10024683E8 1.0 3 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 60 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 61 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 62 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 63 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 65 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 66 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 67 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 68 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 70 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 71 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 72 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 73 0 0 0 0 0 0.0 0.0 0.0 0.0 3.0 75 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 76 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 77 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 78 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 79 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 90 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 91 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 96 0 0 0 0 0 0.0 0.0 0.0 0.0 5.0 100 100 3000 14570 11140 14180 1897431.0 15257.0 62938.0 82567.0 2.0 101 101 2424 6710 4100 7320 584312.0 2868.0 8553.0 12935.0 3.0 102 102 3060 17720 12600 15840 1932081.0 12643.0 33077.0 63570.0 2.0 103 103 5562 9000 7870 9020 1175081.0 7565.0 24622.0 42659.0 3.0 104 104 624 8370 3820 10160 658257.0 3655.0 8273.0 20792.0 2.0 105 105 3150 8590 7130 8470 1042641.0 7468.0 17518.0 31384.0 3.0 106 106 2544 10140 6000 7330 1164956.0 10636.0 45366.0 67045.0 1.0 107 107 3852 9040 7620 8620 1230785.0 10053.0 23110.0 43253.0 3.0 108 108 3888 20220 14780 21130 2263206.0 15173.0 35177.0 65399.0 1.0 109 109 1962 4160 4240 5090 782631.0 6835.0 29191.0 32579.0 3.0 110 110 4620 23270 10930 38260 2410836.0 21921.0 111191.0 87619.0 0.0 0 111 1332 6440 3810 7490 596115.0 2824.0 3245.0 11472.0 0.0 0 112 1344 2490 1790 2460 250951.0 989.0 831.0 5816.0 0.0 0 115 690 1880 750 2900 120178.0 420.0 299.0 2329.0 2.0 120 120 720 11730 6990 10650 1104177.0 8164.0 19952.0 29908.0 1.0 122 122 4392 5570 4130 5090 566792.0 3902.0 7579.0 14745.0 8.0 123 123 3690 5520 4040 4410 640316.0 6422.0 42429.0 36455.0 1.0 124 124 2232 5090 3440 4290 511879.0 5434.0 18268.0 21050.0 1.0 125 125 5250 1720 1460 1390 278982.0 2462.0 16027.0 16113.0 3.0 126 126 1512 1700 1600 1600 321658.0 4552.0 25628.0 19457.0 0.0 0 127 762 150 210 160 24818.0 94.0 190.0 812.0 1.0 130 130 780 4640 2680 3610 398144.0 3220.0 7027.0 15878.0 4.0 133 133 3990 4360 3470 4470 439144.0 2178.0 9489.0 15133.0 1.0 134 134 4824 1790 1640 1810 227607.0 1241.0 7598.0 8975.0 0.0 0 135 2430 1240 1050 1030 143066.0 773.0 4206.0 6599.0 3.0 136 136 4080 2840 2550 3170 310602.0 1358.0 4420.0 12136.0 2.0 137 137 4932 5140 3280 3770 496813.0 4074.0 14707.0 23776.0 3.0 142 142 852 8680 5140 10680 750077.0 3215.0 6657.0 19766.0 3.0 143 143 4290 4960 4090 5540 612770.0 2835.0 5935.0 17180.0 0.0 0 144 864 4650 3090 4710 421055.0 2119.0 3419.0 12072.0 4.0 145 145 3480 14520 12000 18150 2340633.0 15976.0 94626.0 84718.0 2.0 146 146 5256 11110 10920 14040 1810611.0 8907.0 43209.0 63177.0 1.0 147 147 2646 4330 3980 5410 582230.0 2716.0 8801.0 18869.0 4.0 150 150 5400 11740 10440 13400 1730649.0 8516.0 30780.0 57549.0 2.0 151 151 4530 8480 7070 10200 1240121.0 4793.0 18573.0 34434.0 2.0 152 152 6384 11680 10900 14160 1804149.0 9270.0 30818.0 56775.0 3.0 153 153 5508 8400 8050 10730 1547512.0 8065.0 36668.0 56348.0 2.0 154 154 4620 13450 13840 19230 2710097.0 15183.0 63762.0 92712.0 0.0 0 155 930 3970 2180 4880 327997.0 1567.0 1856.0 8399.0 3.0 156 156 5616 11460 11260 14750 1911354.0 9032.0 36270.0 62396.0 1.0 157 157 1884 6710 4830 7320 737147.0 4977.0 11054.0 22435.0 2.0 158 158 3792 9240 8670 12170 1712760.0 10559.0 46914.0 64274.0 0.0 0 159 954 1930 2060 2730 434127.0 3453.0 10123.0 13398.0 6.0 160 160 7680 38600 19470 42160 3565828.0 18523.0 72490.0 107465.0 9.0 161 161 2898 5870 2950 8410 483737.0 1668.0 3881.0 19848.0 2.0 170 170 2040 16200 11780 17270 2301580.0 16368.0 66336.0 111966.0 0.0 0 171 2052 1340 1320 1830 332371.0 2270.0 1

In [0]:
display(prepped)

count zip zipcode sum(zipcode) sum(single_returns) sum(joint_returns) sum(numdep) sum(total_income_amount) sum(taxable_interest_amount) sum(net_capital_gains) sum(biz_net_income) 1009.0 0 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 0 0 0 66430180 52885400 96500590 9.274122025E9 8.271064E7 3.99567789E8 3.10024683E8 1.0 3 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 60 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 61 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 62 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 63 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 65 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 66 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 67 0 0 0 0 0 0.0 0.0 0.0 0.0 4.0 68 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 70 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 71 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 72 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 73 0 0 0 0 0 0.0 0.0 0.0 0.0 3.0 75 0 0 0 0 0 0.0 0.0 0.0 0.0 2.0 76 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 77 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 78 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 79 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 90 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 91 0 0 0 0 0 0.0 0.0 0.0 0.0 1.0 96 0 0 0 0 0 0.0 0.0 0.0 0.0 5.0 100 100 3000 14570 11140 14180 1897431.0 15257.0 62938.0 82567.0 2.0 101 101 2424 6710 4100 7320 584312.0 2868.0 8553.0 12935.0 3.0 102 102 3060 17720 12600 15840 1932081.0 12643.0 33077.0 63570.0 2.0 103 103 5562 9000 7870 9020 1175081.0 7565.0 24622.0 42659.0 3.0 104 104 624 8370 3820 10160 658257.0 3655.0 8273.0 20792.0 2.0 105 105 3150 8590 7130 8470 1042641.0 7468.0 17518.0 31384.0 3.0 106 106 2544 10140 6000 7330 1164956.0 10636.0 45366.0 67045.0 1.0 107 107 3852 9040 7620 8620 1230785.0 10053.0 23110.0 43253.0 3.0 108 108 3888 20220 14780 21130 2263206.0 15173.0 35177.0 65399.0 1.0 109 109 1962 4160 4240 5090 782631.0 6835.0 29191.0 32579.0 3.0 110 110 4620 23270 10930 38260 2410836.0 21921.0 111191.0 87619.0 0.0 0 111 1332 6440 3810 7490 596115.0 2824.0 3245.0 11472.0 0.0 0 112 1344 2490 1790 2460 250951.0 989.0 831.0 5816.0 0.0 0 115 690 1880 750 2900 120178.0 420.0 299.0 2329.0 2.0 120 120 720 11730 6990 10650 1104177.0 8164.0 19952.0 29908.0 1.0 122 122 4392 5570 4130 5090 566792.0 3902.0 7579.0 14745.0 8.0 123 123 3690 5520 4040 4410 640316.0 6422.0 42429.0 36455.0 1.0 124 124 2232 5090 3440 4290 511879.0 5434.0 18268.0 21050.0 1.0 125 125 5250 1720 1460 1390 278982.0 2462.0 16027.0 16113.0 3.0 126 126 1512 1700 1600 1600 321658.0 4552.0 25628.0 19457.0 0.0 0 127 762 150 210 160 24818.0 94.0 190.0 812.0 1.0 130 130 780 4640 2680 3610 398144.0 3220.0 7027.0 15878.0 4.0 133 133 3990 4360 3470 4470 439144.0 2178.0 9489.0 15133.0 1.0 134 134 4824 1790 1640 1810 227607.0 1241.0 7598.0 8975.0 0.0 0 135 2430 1240 1050 1030 143066.0 773.0 4206.0 6599.0 3.0 136 136 4080 2840 2550 3170 310602.0 1358.0 4420.0 12136.0 2.0 137 137 4932 5140 3280 3770 496813.0 4074.0 14707.0 23776.0 3.0 142 142 852 8680 5140 10680 750077.0 3215.0 6657.0 19766.0 3.0 143 143 4290 4960 4090 5540 612770.0 2835.0 5935.0 17180.0 0.0 0 144 864 4650 3090 4710 421055.0 2119.0 3419.0 12072.0 4.0 145 145 3480 14520 12000 18150 2340633.0 15976.0 94626.0 84718.0 2.0 146 146 5256 11110 10920 14040 1810611.0 8907.0 43209.0 63177.0 1.0 147 147 2646 4330 3980 5410 582230.0 2716.0 8801.0 18869.0 4.0 150 150 5400 11740 10440 13400 1730649.0 8516.0 30780.0 57549.0 2.0 151 151 4530 8480 7070 10200 1240121.0 4793.0 18573.0 34434.0 2.0 152 152 6384 11680 10900 14160 1804149.0 9270.0 30818.0 56775.0 3.0 153 153 5508 8400 8050 10730 1547512.0 8065.0 36668.0 56348.0 2.0 154 154 4620 13450 13840 19230 2710097.0 15183.0 63762.0 92712.0 0.0 0 155 930 3970 2180 4880 327997.0 1567.0 1856.0 8399.0 3.0 156 156 5616 11460 11260 14750 1911354.0 9032.0 36270.0 62396.0 1.0 157 157 1884 6710 4830 7320 737147.0 4977.0 11054.0 22435.0 2.0 158 158 3792 9240 8670 12170 1712760.0 10559.0 46914.0 64274.0 0.0 0 159 954 1930 2060 2730 434127.0 3453.0 10123.0 13398.0 6.0 160 160 7680 38600 19470 42160 3565828.0 18523.0 72490.0 107465.0 9.0 161 161 2898 5870 2950 8410 483737.0 1668.0 3881.0 19848.0 2.0 170 170 2040 16200 11780 17270 2301580.0 16368.0 66336.0 111966.0 0.0 0 171 2052 1340 1320 1830 332371.0 2270.0 1

Now that all of our data is prepped. We're going to have to put all of it into one column of a vector type for Spark MLLib. This makes it easy to embed a prediction right in a DataFrame and also makes it very clear as to what is getting passed into the model and what isn't without having to convert it to a numpy array or specify an R formula. This also makes it easy to incrementally add new features, simply by adding to the vector. In the below case rather than specifically adding them in.

In [0]:
nonFeatureCols = ["zip", "zipcode", "count",'distance_to_wealthy']
featureCols = [item for item in prepped.columns if item not in nonFeatureCols]

In [0]:
from pyspark.ml.feature import StringIndexer, OneHotEncoder, StandardScaler

# Convert categorical variables (State -> Numerical)
state_indexer = StringIndexer(inputCol="State", outputCol="State_Index")

# One-hot encode State
state_encoder = OneHotEncoder(inputCol="State_Index", outputCol="State_OHE")

# Normalize income-based features
scaler = StandardScaler(inputCol="AGI", outputCol="AGI_Scaled")


In [0]:
# VectorAssembler Assembles all of these columns into one single vector. To do this, set the input columns and output column. Then that assembler will be used to transform the prepped data to the final dataset.
from pyspark.ml.feature import VectorAssembler

assembler = (VectorAssembler()
  .setInputCols(featureCols)
  .setOutputCol("features"))

finalPrep = assembler.transform(prepped)

Now split the dataset 70-30 for training and testing purposes.A validation set can be created as well, we are omitting it here. It's worth noting that MLLib also supports performing hyperparameter tuning with cross validation and pipelines. All this can be found in [the Databrick's Guide](https://docs.databricks.com).

In [0]:
training, test = finalPrep.randomSplit([0.7, 0.3])

#  Going to cache the data to make sure things stay snappy!
training.cache()
test.cache()

print(training.count()) # Why execute count here??
print(test.count())

4066
1736


# Apache Spark MLLib

At a high level, we're going to create an instance of a `regressor` or `classifier`, that in turn will then be trained and return a `Model` type. Whenever you access Spark MLLib you should be sure to import/train on the name of the algorithm you want as opposed to the `Model` type. For example:

You should import:

`org.apache.spark.ml.regression.LinearRegression`

as opposed to:

`org.apache.spark.ml.regression.LinearRegressionModel`

In the below example, we're going to use linear regression.

The linear regression that is available in Spark MLLib supports an elastic net parameter allowing you to set a threshold of how much you would like to mix l1 and l2 regularization, for [more information on Elastic net regularization see Wikipedia](https://en.wikipedia.org/wiki/Elastic_net_regularization).

As we saw above, we had to perform some preparation of the data before inputting it into the model. We've got to do the same with the model itself. We'll set our hyper parameters, print them out and then finally we can train it! The `explainParams` is a great way to ensure that you're taking advantage of all the different hyperparameters that you have available.

In [0]:
from pyspark.ml.regression import LinearRegression

lrModel = (LinearRegression()
  .setLabelCol("count")
  .setFeaturesCol("features")
  .setElasticNetParam(0.5))

print("Printing out the model Parameters:")
print("-"*20)
print(lrModel.explainParams())
print("-"*20)

Printing out the model Parameters:
--------------------
aggregationDepth: suggested depth for treeAggregate (>= 2). (default: 2)
elasticNetParam: the ElasticNet mixing parameter, in range [0, 1]. For alpha = 0, the penalty is an L2 penalty. For alpha = 1, it is an L1 penalty. (default: 0.0, current: 0.5)
epsilon: The shape parameter to control the amount of robustness. Must be > 1.0. Only valid when loss is huber (default: 1.35)
featuresCol: features column name. (default: features, current: features)
fitIntercept: whether to fit an intercept term. (default: True)
labelCol: label column name. (default: label, current: count)
loss: The loss function to be optimized. Supported options: squaredError, huber. (default: squaredError)
maxBlockSizeInMB: maximum memory in MB for stacking input data into blocks. Data is stacked within partitions. If more than remaining data size in a partition then it is adjusted to the data size. Default 0.0 represents choosing optimal value, depends on specifi

Now finally we can go about fitting our model! You'll see that we're going to do this in a series of steps. First we'll fit it, then we'll use it to make predictions via the `transform` method. This is the same way you would make predictions with your model in the future however in this case we're using it to evaluate how our model is doing. We'll be using regression metrics to get some idea of how our model is performing, we'll then print out those values to be able to evaluate how it performs.

In [0]:
from pyspark.mllib.evaluation import RegressionMetrics
lrFitted = lrModel.fit(training)

In [0]:
%fs ls /databricks-datasets/songs/data-001/

path name size modificationTime dbfs:/databricks-datasets/songs/data-001/header.txt header.txt 377 1454633901000 dbfs:/databricks-datasets/songs/data-001/part-00000 part-00000 52837 1454547464000 dbfs:/databricks-datasets/songs/data-001/part-00001 part-00001 52469 1454547465000 dbfs:/databricks-datasets/songs/data-001/part-00002 part-00002 51778 1454547465000 dbfs:/databricks-datasets/songs/data-001/part-00003 part-00003 50551 1454547465000 dbfs:/databricks-datasets/songs/data-001/part-00004 part-00004 53449 1454547465000 dbfs:/databricks-datasets/songs/data-001/part-00005 part-00005 53301 1454547465000 dbfs:/databricks-datasets/songs/data-001/part-00006 part-00006 54184 1454547465000 dbfs:/databricks-datasets/songs/data-001/part-00007 part-00007 50924 1454547465000 dbfs:/databricks-datasets/songs/data-001/part-00008 part-00008 52533 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00009 part-00009 54570 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00010 part-00010 54338 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00011 part-00011 51836 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00012 part-00012 52297 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00013 part-00013 52044 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00014 part-00014 50704 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00015 part-00015 54158 1454547466000 dbfs:/databricks-datasets/songs/data-001/part-00016 part-00016 50080 1454547467000 dbfs:/databricks-datasets/songs/data-001/part-00017 part-00017 47708 1454547467000 dbfs:/databricks-datasets/songs/data-001/part-00018 part-00018 8858 1454547467000 dbfs:/databricks-datasets/songs/data-001/part-00019 part-00019 53323 1454547467000 dbfs:/databricks-datasets/songs/data-001/part-00020 part-00020 57877 1454547467000 dbfs:/databricks-datasets/songs/data-001/part-00021 part-00021 52491 1454547467000 dbfs:/databricks-datasets/songs/data-001/part-00022 part-00022 54791 1454547467000 dbfs:/databricks-datasets/songs/data-001/part-00023 part-00023 50682 1454547468000 dbfs:/databricks-datasets/songs/data-001/part-00024 part-00024 52863 1454547468000 dbfs:/databricks-datasets/songs/data-001/part-00025 part-00025 47416 1454547468000 dbfs:/databricks-datasets/songs/data-001/part-00026 part-00026 50130 1454547468000 dbfs:/databricks-datasets/songs/data-001/part-00027 part-00027 53462 1454547468000 dbfs:/databricks-datasets/songs/data-001/part-00028 part-00028 54179 1454547468000 dbfs:/databricks-datasets/songs/data-001/part-00029 part-00029 52738 1454547468000 dbfs:/databricks-datasets/songs/data-001/part-00030 part-00030 54159 1454547469000 dbfs:/databricks-datasets/songs/data-001/part-00031 part-00031 51247 1454547469000 dbfs:/databricks-datasets/songs/data-001/part-00032 part-00032 51610 1454547469000 dbfs:/databricks-datasets/songs/data-001/part-00033 part-00033 53895 1454547469000 dbfs:/databricks-datasets/songs/data-001/part-00034 part-00034 53125 1454547469000 dbfs:/databricks-datasets/songs/data-001/part-00035 part-00035 54066 1454547469000 dbfs:/databricks-datasets/songs/data-001/part-00036 part-00036 54265 1454547469000 dbfs:/databricks-datasets/songs/data-001/part-00037 part-00037 54264 1454547470000 dbfs:/databricks-datasets/songs/data-001/part-00038 part-00038 50540 1454547470000 dbfs:/databricks-datasets/songs/data-001/part-00039 part-00039 55193 1454547470000 dbfs:/databricks-datasets/songs/data-001/part-00040 part-00040 54537 1454547470000 dbfs:/databricks-datasets/songs/data-001/part-00041 part-00041 52402 1454547470000 dbfs:/databricks-datasets/songs/data-001/part-00042 part-00042 54673 1454547470000 dbfs:/databricks-datasets/songs/data-001/part-00043 part-00043 53009 1454547470000 dbfs:/databricks-datasets/songs/data-001/part-00044 part-00044 51789 1454547471000 dbfs:/databricks-datasets/songs/data-001/part-00045 part-00045 52986 1454547471000 dbfs:/databricks-datasets/songs/data-001/part-00046 part-00046 54442 1

Now you'll see that since we're working with exact numbers (you can't have 1/2 a farmer's market for example), I'm going to check equality by first rounding the value to the nearest digital value.

In [0]:
holdout = (lrFitted
  .transform(test)
  .selectExpr("prediction as raw_prediction", 
    "double(round(prediction)) as prediction", 
    "count", 
    """CASE double(round(prediction)) = count 
  WHEN true then 1
  ELSE 0
END as equal"""))

display(holdout)

raw_prediction prediction count equal 1.650102381516466 2.0 0.0 0 1.3295046135694208 1.0 0.0 0 1.6100909697991914 2.0 0.0 0 1.4991630468288157 1.0 0.0 0 1.4171628261507605 1.0 0.0 0 1.2244704000958662 1.0 0.0 0 1.6135293951958718 2.0 1.0 0 1.3994024918528112 1.0 1.0 1 1.232267098659754 1.0 1.0 1 1.4676134435940933 1.0 1.0 1 1.2575860051655003 1.0 1.0 1 1.70775416412802 2.0 4.0 0 3.5490021016219577 4.0 5.0 0 2.0275279608549717 2.0 5.0 0 1.582805031263639 2.0 0.0 0 1.2338895964038583 1.0 0.0 0 1.2773122800129864 1.0 0.0 0 1.6250086322536077 2.0 1.0 0 0.6672032541228069 1.0 4.0 0 1.3196738292084165 1.0 5.0 0 1.692191329943863 2.0 0.0 0 1.4617431289947014 1.0 0.0 0 1.5632933387267662 2.0 0.0 0 1.5855467872778084 2.0 0.0 0 0.9795481685007856 1.0 1.0 1 1.502756152079003 2.0 1.0 0 2.032135796900737 2.0 2.0 1 2.5482854023437227 3.0 2.0 0 1.3619525004518858 1.0 0.0 0 1.3770834337102549 1.0 0.0 0 1.7922513982469352 2.0 2.0 1 1.5478181661586394 2.0 2.0 1 1.3410048099850527 1.0 2.0 0 1.586880824848731 2.0 0.0 0 1.6745134380002753 2.0 0.0 0 1.4777335865766537 1.0 0.0 0 1.3087169512487273 1.0 1.0 1 1.3363603697565147 1.0 1.0 1 1.3361445547869764 1.0 1.0 1 1.466154568192729 1.0 2.0 0 1.1381175631166625 1.0 2.0 0 1.291297772582625 1.0 3.0 0 0.9175674044898305 1.0 3.0 0 1.8041304973291594 2.0 0.0 0 1.6060733694838405 2.0 1.0 0 0.8802499186329622 1.0 1.0 1 1.085646562707378 1.0 1.0 1 1.9796316869382469 2.0 2.0 1 1.4697431521169217 1.0 2.0 0 1.2792559393986185 1.0 2.0 0 1.5207414012142144 2.0 2.0 1 1.803438938007338 2.0 7.0 0 1.5551137181847614 2.0 0.0 0 1.333409857934068 1.0 0.0 0 1.5493226837973921 2.0 0.0 0 1.3624606966020023 1.0 1.0 1 1.6232726659708243 2.0 1.0 0 -1.0278202644804892 -1.0 1.0 0 1.459655392152483 1.0 1.0 1 1.8250157071565796 2.0 2.0 1 2.589566822482432 3.0 2.0 0 1.4213165930553182 1.0 2.0 0 5.101924737558274 5.0 7.0 0 1.3367627635958916 1.0 0.0 0 1.8677889229984954 2.0 0.0 0 1.805501161410482 2.0 0.0 0 1.3978342031883013 1.0 0.0 0 1.7204245554293949 2.0 1.0 0 1.7464561547543536 2.0 1.0 0 1.3504365125694546 1.0 1.0 1 1.1026130198966126 1.0 1.0 1 1.022399420246749 1.0 1.0 1 1.4656414752819362 1.0 0.0 0 1.5783715811275063 2.0 1.0 0 1.6845788072383605 2.0 3.0 0 1.1561638579830937 1.0 4.0 0 1.499591760945242 1.0 0.0 0 1.479676702528267 1.0 0.0 0 1.4743069816201033 1.0 0.0 0 1.840983700767723 2.0 1.0 0 1.52372951398746 2.0 1.0 0 1.4321557096134727 1.0 1.0 1 1.5136227643500968 2.0 1.0 0 1.5957127889729614 2.0 2.0 1 1.3647059075564743 1.0 3.0 0 1.5314686216046294 2.0 0.0 0 1.6160085545858571 2.0 0.0 0 1.4712493381808962 1.0 1.0 1 1.3577955382105955 1.0 1.0 1 1.7719022271089793 2.0 2.0 1 1.7660161630209108 2.0 3.0 0 1.5966737669472073 2.0 3.0 0 1.2571048460215206 1.0 1.0 1 1.7412245866781184 2.0 2.0 1 1.6192597986779063 2.0 2.0 1 2.0975842200347814 2.0 3.0 0 1.1101989123456744 1.0 3.0 0 3.4974463719247564 3.0 9.0 0 1.6932233379827124 2.0 0.0 0 1.5458908361454835 2.0 0.0 0 1.6046369857904166 2.0 0.0 0 1.6299006302252796 2.0 1.0 0 0.20930815863304186 0.0 1.0 0 1.4293112368691925 1.0 1.0 1 1.7028567712947997 2.0 3.0 0 1.592228516034584 2.0 0.0 0 1.62279667999673 2.0 0.0 0 1.4465634964141343 1.0 1.0 1 1.6449864502313378 2.0 1.0 0 1.3374090618529886 1.0 1.0 1 1.5012625979435001 2.0 1.0 0 1.7516579440567128 2.0 2.0 1 1.2799062922017863 1.0 2.0 0 1.3750963906332898 1.0 2.0 0 1.664397841513468 2.0 0.0 0 1.4276264317166807 1.0 0.0 0 1.3484218320216284 1.0 0.0 0 1.3856668156176657 1.0 0.0 0 1.2120071530638596 1.0 1.0 1 1.4061955094684957 1.0 1.0 1 1.2444874033776525 1.0 1.0 1 1.0965890956939464 1.0 2.0 0 1.3839462988780735 1.0 3.0 0 1.564251614059957 2.0 4.0 0 1.839852521581301 2.0 0.0 0 1.7491676329599828 2.0 0.0 0 1.4553765300124277 1.0 0.0 0 1.4096187611030535 1.0 0.0 0 1.58190990226886 2.0 1.0 0 1.613395610340223 2.0 1.0 0 1.3873591279565807 1.0 1.0 1 1.2482648652237853 1.0 1.0 1 1.9424899973309544 2.0 2.0 1 1.460717994747019 1.0 3.0 0 1.8063639632451935 2.0 3.0 0 1.135638758928372 1.0 0.0 0 1.114838961277992 1.0 0.0 0 1.4316600995203679 1.0

Now let's see what proportion was exactly correct.

In [0]:
display(holdout.selectExpr("sum(equal)/sum(1)"))

(sum(equal) / sum(1)) 0.2540322580645161

In [0]:
# have to do a type conversion for RegressionMetrics
rm = RegressionMetrics(holdout.select("prediction", "count").rdd.map(lambda x:  (x[0], x[1])))

print("MSE: ", rm.meanSquaredError)
print("MAE: ", rm.meanAbsoluteError)
print("RMSE Squared: ", rm.rootMeanSquaredError)
print("R Squared: ", rm.r2)
print("Explained Variance: ", rm.explainedVariance, "\n")

/databricks/spark/python/pyspark/sql/context.py:164: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(


MSE:  2.673387096774194
MAE:  1.169930875576037
RMSE Squared:  1.6350495701275218
R Squared:  0.012849365716335548
Explained Variance:  0.5866736392788127 



These results appear to be sub-optimal, so let's try exploring another way to train the model. Rather than training on a single model with hard-coded parameters, let's train using a [pipeline](http://spark.apache.org/docs/latest/api/scala/index.html#org.apache.spark.ml.Pipeline). 

A pipeline is going to give us some nice benefits in that it will allow us to use a couple of transformations we need in order to transform our raw data into the prepared data for the model but also it provides a simple, straightforward way to try out a lot of different combinations of parameters. This is a process called [hyperparameter tuning](https://en.wikipedia.org/wiki/Hyperparameter_optimization) or grid search. To review, grid search is where you set up the exact parameters that you would like to test and MLLib will automatically create all the necessary combinations of these to test.

For example, below we'll set `numTrees` to 20 and 60 and `maxDepth` to 5 and 10. The parameter grid builder will automatically construct all the combinations of these two variable (along with the other ones that we might specify too). Additionally we're also going to use [cross validation](https://en.wikipedia.org/wiki/Cross-validation_(statistics)) to tune our hyperparameters, this will allow us to attempt to try to control [overfitting](https://en.wikipedia.org/wiki/Overfitting) of our model.

Lastly we'll need to set up a [Regression Evaluator](http://spark.apache.org/docs/latest/api/scala/index.html#org.apache.spark.ml.evaluation.RegressionEvaluator) that will evaluate the models that we choose based on some metric (the default is RMSE). The key take away is that the pipeline will automatically optimize for our given metric choice by exploring the parameter grid that we set up rather than us having to do it manually like we would have had to do above.

Now we can go about training our random forest! 

*note: this might take a little while because of the number of combinations that we're trying and limitations in workers available.*

In [0]:
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline

# Define the Random Forest Regressor
rfModel = RandomForestRegressor(labelCol="count", featuresCol="features")

# Define the parameter grid for hyperparameter tuning
paramGrid = (ParamGridBuilder()
  .addGrid(rfModel.maxDepth, [5, 10])  # Testing different tree depths
  .addGrid(rfModel.numTrees, [20, 50])  # Testing different numbers of trees
  .build())

# Define the pipeline with the model
pipeline = Pipeline(stages=[rfModel])

# Set up cross-validation
cv = CrossValidator(
    estimator=pipeline,  # The model pipeline
    estimatorParamMaps=paramGrid,  # The parameter grid
    evaluator=RegressionEvaluator(labelCol="count", metricName="rmse"),  # Evaluating using RMSE
    numFolds=3  # 3-fold cross-validation
)

# Train the model using cross-validation
pipelineFitted = cv.fit(training)

# Make predictions on the test set
predictions = pipelineFitted.transform(test)

# Evaluate the model on test data
evaluator = RegressionEvaluator(labelCol="count", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)

# Print the final RMSE
print(f"Test RMSE: {rmse}")


Now we've trained our model! Let's take a look at which version performed best!

In [0]:
print("The Best Parameters:\n--------------------")
print(pipelineFitted.bestModel.stages[0])
pipelineFitted.bestModel.stages[0].extractParamMap()

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

As well as our regression metrics on the test set.

In [0]:
%fs


com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
pipelineFitted.bestModel

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
holdout2 = (pipelineFitted.bestModel
  .transform(test)
  .selectExpr("prediction as raw_prediction", 
    "double(round(prediction)) as prediction", 
    "count", 
    """CASE double(round(prediction)) = count 
  WHEN true then 1
  ELSE 0
END as equal"""))
  
display(holdout2)

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
rm2 = RegressionMetrics(holdout2.select("prediction", "count").rdd.map(lambda x:  (x[0], x[1])))

print("MSE: ", rm2.meanSquaredError)
print("MAE: ", rm2.meanAbsoluteError)
print("RMSE Squared: ", rm2.rootMeanSquaredError)
print("R Squared: ", rm2.r2)
print("Explained Variance: ", rm2.explainedVariance, "\n")

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

Finally we'll see an improvement in our "exactly right" proportion as well!

In [0]:
display(holdout2.selectExpr("sum(equal)/sum(1)"))

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data